In [22]:
words = open('names.txt').read().splitlines()

In [23]:
chars = sorted(list(set(''.join(words))))
stoi = {s:i+1 for i, s in enumerate(chars)}
stoi['.'] = 0
itos = {i:s for s, i in stoi.items()}

In [55]:
import torch
import torch.nn.functional as F

In [76]:
block_size = 3
X, Y = [], []
for w in words:
    print(w)
    context = [0] * block_size

    for c in w + '.':
        ix = stoi[c]
        X.append(context)
        Y.append(ix)

        print(''.join(itos[i] for i in context), '---->', itos[ix])
        context = context[1:] + [ix]

X = torch.tensor(X)
Y = torch.tensor(Y)

emma
... ----> e
..e ----> m
.em ----> m
emm ----> a
mma ----> .
olivia
... ----> o
..o ----> l
.ol ----> i
oli ----> v
liv ----> i
ivi ----> a
via ----> .
ava
... ----> a
..a ----> v
.av ----> a
ava ----> .
isabella
... ----> i
..i ----> s
.is ----> a
isa ----> b
sab ----> e
abe ----> l
bel ----> l
ell ----> a
lla ----> .
sophia
... ----> s
..s ----> o
.so ----> p
sop ----> h
oph ----> i
phi ----> a
hia ----> .
charlotte
... ----> c
..c ----> h
.ch ----> a
cha ----> r
har ----> l
arl ----> o
rlo ----> t
lot ----> t
ott ----> e
tte ----> .
mia
... ----> m
..m ----> i
.mi ----> a
mia ----> .
amelia
... ----> a
..a ----> m
.am ----> e
ame ----> l
mel ----> i
eli ----> a
lia ----> .
harper
... ----> h
..h ----> a
.ha ----> r
har ----> p
arp ----> e
rpe ----> r
per ----> .
evelyn
... ----> e
..e ----> v
.ev ----> e
eve ----> l
vel ----> y
ely ----> n
lyn ----> .
abigail
... ----> a
..a ----> b
.ab ----> i
abi ----> g
big ----> a
iga ----> i
gai ----> l
ail ----> .
emily
... ----> e
..e ---

In [26]:
C = torch.randn((27, 2))

In [27]:
emb = C[X]
emb.shape

torch.Size([32, 3, 2])

In [28]:
W1 = torch.randn((6, 100))
B1 = torch.randn(100)

In [29]:
h = torch.tanh(emb.view(emb.shape[0], 6) @ W1 + B1)

In [30]:
W2 = torch.randn((100, 27))
B2 = torch.randn(27)


In [34]:
logits = h @ W2 + B2
logits

tensor([[ -3.5630,   8.1167,  -2.4068,  -7.0183,  -4.6002,   5.8853,  -4.6151,
          -4.7871,   4.3302,  -7.6783,   8.2437,   7.4931,   5.8198,   8.2866,
         -11.0716,  -0.1544,  -3.5504,  -1.7793, -10.5455,  -3.8526,   5.7081,
           1.3067,  -1.0345,   2.6426,   2.7764,  -3.7031,   7.0091],
        [  3.3372,   4.7938,   2.7945,  -8.6640,   0.5067,   1.6964,  -1.5381,
          -0.5848,   4.6229,  -8.7349,  10.1125,   5.5113,   9.9671,   1.3170,
         -11.8829,  -3.1693,  -3.3327,  -4.7474,  -9.2143,  -6.8039,   1.3305,
          10.2700,   7.0911,  -1.2971,  -2.6829, -13.1339,  -3.8300],
        [ -3.2594,  -5.5325,  -2.9347,   0.5188,  -1.6500, -12.9721,  -8.1873,
          -0.1698, -10.5951,  -6.7234,  26.4100,   4.3707,   4.5303,   4.6887,
          -0.9791,   8.0370, -10.2001,  -1.7328,   0.7660,  10.7683,   7.6895,
           9.4632,  -2.4356,   2.5977,  -4.0762,  -1.2834,  -6.7401],
        [  1.9463,  -2.9817,   5.2991,   4.6869,   8.2651,  -9.7954,   3.1322,


In [36]:
counts = logits.exp()

In [39]:
prob = counts / counts.sum(1, keepdim=True)
prob.shape

torch.Size([32, 27])

In [42]:
loss = -prob[torch.arange(32), Y].log().mean()
loss

tensor(15.1318)

In [223]:
g = torch.Generator().manual_seed(2147483647)
C = torch.randn((27, 2), generator=g)
W1 = torch.randn((6, 100), generator=g)
b1 = torch.randn(100, generator=g)
W2 = torch.randn((100, 27), generator=g)
b2 = torch.randn(27, generator=g)
parameters = [C, W1, b1, W2, b2]

for p in parameters: p.requires_grad = True

In [144]:
sum(p.nelement() for p in parameters)

3481

In [379]:
# forward pass
for _ in range(10000):
    # minibatch 
    ix = torch.randint(0, X.shape[0], (32,))


    emb = C[X[ix]]
    h = torch.tanh(emb.view(-1, 6) @ W1 + b1)
    logits = h @ W2 + b2
    loss = F.cross_entropy(logits, Y[ix])
    print(loss.item())

    for p in parameters:
        p.grad = None

    loss.backward()

    for p in parameters:
        p.data += -0.01 * p.grad


3.8534200191497803
3.118807792663574
2.660978078842163
3.1473662853240967
2.950753927230835
2.9191133975982666
3.2041127681732178
3.365269184112549
3.065269947052002
3.8037095069885254
3.446345090866089
3.7806777954101562
3.482997417449951
3.0916430950164795
3.1719369888305664
3.358424425125122
2.583146810531616
2.565424680709839
2.9695627689361572
3.1116092205047607
3.260582208633423
2.8593127727508545
2.937264919281006
2.714388608932495
3.784644365310669
3.3568966388702393
3.3160760402679443
3.388491153717041
3.6330344676971436
2.9938747882843018
2.9983482360839844
2.733959197998047
3.304845094680786
2.8205878734588623
3.065706253051758
2.8455653190612793
3.0497941970825195
4.0929856300354
3.551704168319702
2.875875473022461
2.6602277755737305
2.966440200805664
2.987802505493164
3.5031020641326904
3.1063709259033203
2.525676965713501
2.839787721633911
3.5377557277679443
3.6634960174560547
3.197481393814087
3.0476558208465576
4.217363357543945
2.849910259246826
3.526927947998047
4.003

In [380]:
emb = C[X]
h = torch.tanh(emb.view(-1, 6) @ W1 + b1)
logits = h @ W2 + b2
loss = F.cross_entropy(logits, Y)

In [381]:
loss.item()

2.5574727058410645

In [56]:
F.cross_entropy(logits, Y)

tensor(17.7697)